In [47]:
import joblib
import os
import itertools
import re
import unidecode
import string

import numpy as np
import pandas as pd

from collections import defaultdict
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics import confusion_matrix
from sklearn.preprocessing import normalize
from tqdm import tqdm

import matplotlib.pyplot as plt
%matplotlib inline

In [59]:
def measure_cosine_similarity(hdv1, hdv2):
    return(cosine_similarity([hdv1], [hdv2]))

def jobsave(object_to_save, filename):
    joblib.dump(object_to_save, filename)

def jobload(filename):
    return joblib.load(filename)

def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues,
                          x_label='True label',
                          y_label='Predicted label'
                         ):
    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=45)
    plt.yticks(tick_marks, classes)
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')
    print(cm)
    thresh = cm.max() / 2.
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plt.text(j, i, cm[i, j],
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black")
    plt.tight_layout()
    plt.ylabel(x_label)
    plt.xlabel(y_label);

In [28]:
nor_lang_train = jobload('nor_lang_train.jbl')

HD_array = []
HD_array_keys = []
for key in nor_lang_train:
    HD_array_keys.append(key)
    HD_array.append(nor_lang_train[key])
HD_array = np.array(HD_array)
HD_array = np.reshape(HD_array, [21, 1000])

In [5]:
test_keys = {
    'bg' : 'Bulgarian',
    'cs' : 'Czech',
    'da' : 'Danish',
    'de' : 'German',
    'el' : 'Greek',
    'en' : 'English',
    'et' : 'Estonian',
    'fi' : 'Finnish',
    'fr' : 'French',
    'hu' : 'Hungarian',
    'it' : 'Italian',
    'lv' : 'Latvian',
    'lt' : 'Lithuanian',
    'nl' : 'Dutch',
    'pl' : 'Polish',
    'pt' : 'Portuguese',
    'ro' : 'Romanian',
    'sk' : 'Slovak',
    'sl' : 'Slovene',
    'es' : 'Spanish',
    'sv' : 'Swedish'
}

In [6]:
test_data_root = 'encoded_langs_test'
data_lang_paths = os.listdir(test_data_root)

In [ ]:
cosine_similarity(HD_array, [test_block])

In [16]:
lang_paths_test = defaultdict()
for path in data_lang_paths:
    lang_paths_test[path[:2]] = os.path.join(test_data_root, path)

In [36]:
gt = []
prediction = []

for key in lang_paths_test.keys():
    true_lang = test_keys[key]
    lang_blocks = jobload(lang_paths_test[key])
    for tb in tqdm(range(len(lang_blocks))):
        test_block = lang_blocks[tb]
        gt.append(true_lang)
        pred_lang = HD_array_keys[cosine_similarity(HD_array, test_block).argmax()]
        prediction.append(pred_lang)
    del lang_blocks

100%|██████████| 1851574/1851574 [20:06<00:00, 1534.64it/s]


In [37]:
jobsave([gt, prediction], 'test_1_gt_results.jbl')

In [39]:
from sklearn import metrics

In [40]:
print(metrics.confusion_matrix(gt, prediction))

[[ 391158    2114      73     453     188     185     232     180     412
      279     140     621     185     213    2287     602     283    1864
     2561     144      86]
 [   4830  568272    2007     603     575    1065     469     774     345
     2044     676    1110     842     583    1066     899     825   39457
    16223     475     196]
 [    865    1170 1855638   15675    2469    2135    2803    6648    5196
      859     658    1700    1364    1014    3645    1021    1703    1252
      967    1251   52897]
 [    281     300   11323 1937022    2702     856    1121    5180    9966
      774    1961     509     614    1058    1660    2639    2645     443
      364    4370    3466]
 [     98    1341     772    1415  378122     406     294    3534     617
     1188     817    1190     358    1039     151    1935    1498     364
       88     720     772]
 [    733     596     165     506     268  629096    4696    1531    2061
     1716     280     597    1514     891     330  

In [ ]:
cnf_matrix = confusion_matrix(gt, prediction, labels=HD_array_keys)

In [71]:
plt.figure(figsize = (23, 17), dpi=500)
plot_confusion_matrix(cnf_matrix, classes=HD_array_keys,
                      title='T1:Bipolar vectors experiment. Overall accuracy: {:.3f}'.format(
                          np.diag(cnf_matrix).sum() / cnf_matrix.sum()
                      ),
                      x_label='True language',
                      y_label='Predicted language'
                     );

Confusion matrix, without normalization
[[ 391158    2114      73     412     279     188     185     232     180
      140     621     185     213     453    2287     602     283    1864
     2561     144      86]
 [   4830  568272    2007     345    2044     575    1065     469     774
      676    1110     842     583     603    1066     899     825   39457
    16223     475     196]
 [    865    1170 1855638    5196     859    2469    2135    2803    6648
      658    1700    1364    1014   15675    3645    1021    1703    1252
      967    1251   52897]
 [    426     747    4481 1861266    4657    2476    2897    4215    9266
      840     713    3889     552    8040     943     760    1353    1472
      326     700    3525]
 [   4374    1616     174     954 1194129    3342     498    1807     779
     1597    2397    2354    2086    2145    1818    1277     882    1557
      231    1023     516]
 [     98    1341     772     617    1188  378122     406     294    3534
      817  

In [65]:
t1_report = metrics.classification_report(gt, prediction, digits=3)

In [67]:
print(t1_report)

              precision    recall  f1-score   support

   Bulgarian      0.907     0.968     0.936    404260
       Czech      0.877     0.883     0.880    643336
      Danish      0.965     0.946     0.956   1960930
       Dutch      0.967     0.974     0.970   1989254
     English      0.936     0.953     0.945    396719
    Estonian      0.936     0.970     0.953    648497
     Finnish      0.982     0.972     0.977   1911877
      French      0.969     0.959     0.964   2000064
      German      0.977     0.973     0.975   1913544
       Greek      0.971     0.974     0.973   1225556
   Hungarian      0.973     0.967     0.970    621758
     Italian      0.968     0.975     0.972   1899011
     Latvian      0.917     0.940     0.928    634878
  Lithuanian      0.941     0.941     0.941    630951
      Polish      0.952     0.970     0.961    629127
  Portuguese      0.958     0.963     0.961   1950373
    Romanian      0.880     0.973     0.924    396671
      Slovak      0.886    

In [49]:
test_keys = {
    'bul' : 'Bulgarian',
    'ces' : 'Czech',
    'dan' : 'Danish',
    'deu' : 'German',
    'ell' : 'Greek',
    'eng' : 'English',
    'est' : 'Estonian',
    'fin' : 'Finnish',
    'fra' : 'French',
    'hun' : 'Hungarian',
    'ita' : 'Italian',
    'lav' : 'Latvian',
    'lit' : 'Lithuanian',
    'nld' : 'Dutch',
    'pol' : 'Polish',
    'por' : 'Portuguese',
    'ron' : 'Romanian',
    'slk' : 'Slovak',
    'slv' : 'Slovene',
    'spa' : 'Spanish',
    'swe' : 'Swedish'
}

13102

In [50]:
train_keys = {
    'bul' : 'Bulgarian',
    'ces' : 'Czech',
    'dan' : 'Danish',
    'deu' : 'German',
    'ell' : 'Greek',
    'eng' : 'English',
    'est' : 'Estonian',
    'fin' : 'Finnish',
    'fra' : 'French',
    'hun' : 'Hungarian',
    'ita' : 'Italian',
    'lav' : 'Latvian',
    'lit' : 'Lithuanian',
    'nld' : 'Dutch',
    'pol' : 'Polish',
    'por' : 'Portuguese',
    'ron' : 'Romanian',
    'slk' : 'Slovak',
    'slv' : 'Slovene',
    'spa' : 'Spanish',
    'swe' : 'Swedish'
}

404260

In [77]:
test_range = np.linspace(-1, 1, 20001)

In [92]:
a = test_range[2]
b = img_counterpart(a)
(a**2 + b**2)**0.5 

1.0

In [64]:
import cmath

In [79]:
len(test_range)

20001

In [89]:
def img_counterpart(real):
    img_pos = (1- real**2)**0.5
    
    return img_pos

In [90]:
img_counterpart(0.12)

0.9927738916792685

In [115]:
HD_array_keys[0]

'Bulgarian'

In [84]:
gt_2 = []
prediction_2 = []

for key in lang_paths_test.keys():
    true_lang = test_keys[key]
    lang_blocks = jobload(lang_paths_test[key])
    for tb in tqdm(range(1000)):
        test_block = lang_blocks[tb]
        gt_2.append(true_lang)
        pred_lang = HD_array_keys[cosine_similarity(HD_array, test_block).argmax()]
        prediction_2.append(pred_lang)
    del lang_blocks

100%|██████████| 1000/1000 [00:00<00:00, 1432.83it/s]


FileNotFoundError: [Errno 2] No such file or directory: 'encoded_langs_test\\de_encoded_test.jbl'

In [85]:
cnf_matrix_2 = confusion_matrix(gt_2, prediction_2, labels=HD_array_keys)

In [86]:
plt.figure(figsize = (23, 17), dpi=500)
plot_confusion_matrix(cnf_matrix_2, classes=HD_array_keys,
                      title='T1:Bipolar vectors experiment. Overall accuracy: {:.3f}'.format(
                          np.diag(cnf_matrix).sum() / cnf_matrix.sum()
                      ),
                      x_label='True language',
                      y_label='Predicted language'
                     );

Confusion matrix, without normalization
[[587  57   1  48   7  47  15  26  20  15  41  12   8  10  22   8   4  37
    5  29   1]
 [  7 637   0  31   7  39   6  18  27   9  25   6   6   3  14   3   1  94
   34  33   0]
 [  0   3 950   4   0   0   2   2   7   0   0   0   0   5   0   3   0   1
    2   0  21]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0
    0   0   0]
 [  0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0   0 

In [87]:
t1_report_2 = metrics.classification_report(gt_2, prediction_2, digits=3)

C:\Users\Tim\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1272: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [88]:
print(t1_report_2)

              precision    recall  f1-score   support

   Bulgarian      0.988     0.587     0.737      1000
       Czech      0.914     0.637     0.751      1000
      Danish      0.999     0.950     0.974      1000
       Dutch      0.000     0.000     0.000         0
     English      0.000     0.000     0.000         0
    Estonian      0.000     0.000     0.000         0
     Finnish      0.000     0.000     0.000         0
      French      0.000     0.000     0.000         0
      German      0.000     0.000     0.000         0
       Greek      0.000     0.000     0.000         0
   Hungarian      0.000     0.000     0.000         0
     Italian      0.000     0.000     0.000         0
     Latvian      0.000     0.000     0.000         0
  Lithuanian      0.000     0.000     0.000         0
      Polish      0.000     0.000     0.000         0
  Portuguese      0.000     0.000     0.000         0
    Romanian      0.000     0.000     0.000         0
      Slovak      0.000    

In [80]:
(a**2 + b**2)**0.5

1.0

In [83]:
a/b

2.0

In [82]:
b

0.4472135954999579